In [3]:
import pandas as pd
import numpy as np
import joblib 

In [332]:
# Load necessary components
# Load necessary components
scaler = joblib.load('scaler.pkl')
selector = joblib.load('pca.pkl')
best_pipeline = joblib.load('best_model_pipeline.pkl')

submissions = pd.read_csv('created+data/SampleSubmission2023.csv')
team_data = pd.read_csv('data/2024_teamData.csv')

columns_to_remove = ['School', 'Conf', 'TeamName','PF', 'PA', 'NumOT', 'FGM', 'FGA', 'FGM3', 'FGA3',
       'FTM', 'FTA', 'OR', 'DR', 'Ast', 'TO', 'Stl', 'Blk', 'Fls', 'OppFGM',
       'OppFGA', 'OppFGM3', 'OppFGA3', 'OppFTM', 'OppFTA', 'OppOR', 'OppDR',
       'OppAst', 'OppTO', 'OppStl', 'OppBlk', 'OppFls', 'Wins', 'Loses',  'Tempo_x',
       'TO_per_poss_last_6_last_6', 'Stl_per_poss_last_6_last_6',
       'Blk_per_poss_last_6_last_6', 'PF_per_poss_last_6_last_6', 'FGM3_per_poss_last_6_last_6', 
       'FGA3_per_poss_last_6_last_6', 'Possessions_last_6_last_6',
       'FTM_per_poss_last_6_last_6', 'FTA_per_poss_last_6_last_6',
       'Score_per_poss_last_6_last_6', 'OR_per_poss_last_6_last_6',]

team_data['Trapezoid'] = team_data['AdjEM'] - team_data['Tempo_x']
team_data['Diff Win'] = team_data['Win_last_6'] - team_data['Win %'] 
team_data['3PM_diff'] =team_data['3PTPPos'] - team_data['FGA3_per_poss_last_6_last_6']
team_data['FT_diff'] = team_data['FTPPos'] - team_data['FTM_per_poss_last_6_last_6']
team_data['PPPos_diff'] = team_data['PPPos'] - team_data['PF_per_poss_last_6_last_6']
team_data['Orb_diff'] = team_data['ORPPos'] - team_data['OR_per_poss_last_6_last_6']
team_data['Tov_diff'] = team_data['TOV %'] - team_data['TO_per_poss_last_6_last_6']
team_data['rank_diff'] = team_data['Week_18'] - team_data['Week_1']
team_data['Pom_diff'] = team_data['AdjOE'] - team_data['AdjDE']
team_data['TOV Margin'] = team_data['TOV %'] - team_data['TOV Forced %']

team_data.drop(columns=columns_to_remove, inplace=True)

In [333]:
seeds = pd.read_csv('data/MNCAATourneySeeds.csv')
seeds['Seed'] = seeds['Seed'].apply(lambda x: int(x[1:3]))
data2024 = pd.merge(team_data, seeds, on=['Season', 'TeamID'], how='left')


In [334]:
data2024

Season  TeamID  Games Played  Minutes Played  Possesions  OppPossesions  \
0      2024    1101            31            1255     2240.68        2197.12   
1      2024    1102            31            1250     1947.00        2000.28   
2      2024    1103            32            1285     2153.64        2145.76   
3      2024    1104            32            1290     2418.20        2406.80   
4      2024    1105            33            1325     2379.60        2376.80   
..      ...     ...           ...             ...         ...            ...   
356    2024    1474            31            1240     2304.32        2288.64   
357    2024    1475            29            1165     2025.72        2031.52   
358    2024    1476            30            1205     2093.92        2098.84   
359    2024    1477            30            1245     2128.12        2111.88   
360    2024    1478            29            1165     1991.76        1992.44   

        Win %     PPPos    PAPPos  PPPos Margin  ...  Diff Win  3PM_diff  \
0    0.451613  0.981845  1.038632     -0.056788  ...  0.215054 -0.104629   
1    0.290323  1.053416  1.121343     -0.067928  ... -0.123656 -0.274279   
2    0.687500  1.074924  0.996384      0.078541  ... -0.020833 -0.244118   
3    0.656250  1.200893  1.077780      0.123114  ... -0.322917 -0.209681   
4    0.333333  0.952681  1.052255     -0.099574  ...  0.166667 -0.166395   
..        ...       ...       ...           ...  ...       ...       ...   
356  0.387097  1.040220  1.118568     -0.078348  ...  0.279570 -0.241481   
357  0.172414  0.958178  1.070135     -0.111957  ... -0.005747 -0.225775   
358  0.100000  0.905479  1.103467     -0.197988  ...  0.066667 -0.291713   
359  0.333333  0.948255  1.088130     -0.139875  ...  0.166667 -0.210152   
360  0.413793  1.018697  1.040433     -0.021736  ...  0.086207 -0.274239   

      FT_diff  PPPos_diff  Orb_diff  Tov_diff  rank_diff  Pom_diff  \
0   -0.005506    0.729084 -0.012658 -0.006473        0.0   -4.1870   
1    0.025635    0.743036  0.021355  0.011490        0.0   -7.1860   
2    0.003145    0.815470  0.002817 -0.013349        0.0    4.9370   
3    0.003578    0.906736  0.022210  0.015957       -8.0   22.4830   
4   -0.010513    0.672598 -0.006414 -0.000338        0.0  -15.4477   
..        ...         ...       ...       ...        ...       ...   
356 -0.016354    0.807534 -0.014293  0.008633        0.0   -7.8130   
357 -0.017293    0.644991 -0.000076  0.032776        0.0  -15.7904   
358  0.002158    0.690979 -0.013669  0.031737        0.0  -22.8936   
359 -0.062200    0.719921 -0.010582  0.017305        0.0  -16.3119   
360 -0.014718    0.778055  0.003683 -0.016359        0.0  -10.9090   

     TOV Margin  Seed  
0      0.026266   NaN  
1      0.009055   NaN  
2      0.038091  14.0  
3      0.005907   4.0  
4      0.052342   NaN  
..          ...   ...  
356    0.023874   NaN  
357    0.056640   NaN  
358    0.062374   NaN  
359   -0.014451   NaN  
360    0.008084   NaN  

[361 rows x 63 columns]

In [338]:
data2024['Seed'] = data2024['Seed'].fillna(100)
columns_to_remove = ['Games Played', 'Minutes Played', 'Possesions', 'OppPossesions', 
                     'DE', 'RankDE', 'Week_6', 'Week_12','RankAdjEM', 'AdjTempo',
                    'OE', 'RankOE', 'RankAdjDE', 'RankAdjOE', 'Tempo_y', 'RankTempo', 'RankAdjTempo']
data2024.drop(columns=columns_to_remove, inplace=True)

/var/folders/bm/x9qxxjrx0fx_4fw8sspqvjgh0000gn/T/ipykernel_2909/3115232555.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data2024['Seed'] = data2024['Seed'].fillna(100)


KeyError: "['Games Played', 'Minutes Played', 'Possesions', 'OppPossesions', 'DE', 'RankDE', 'Week_6', 'Week_12', 'RankAdjEM', 'AdjTempo', 'OE', 'RankOE', 'RankAdjDE', 'RankAdjOE', 'Tempo_y', 'RankTempo', 'RankAdjTempo'] not found in axis"

In [339]:
new_order = ['Season', 'TeamID', 'Win %', 'PPPos', 'PAPPos', 'PPPos Margin', 'FG %', 'OppFG%',
       '3PT FG %', '3PTPPos', 'FT %', 'FTPPos', 'OppFTPPos', 'ORPPos',
       'Opp ORPPos', 'DRPG', 'REBPG', 'REB Margin', 'True Shooting %',
       'Effective FG%', 'TOV %', 'TOV Forced %', 'Foul Margin', 'OppEFG',
       'Win_last_6', 'FGM_per_poss_last_6_last_6',
       'FGA_per_poss_last_6_last_6', 'DR_per_poss_last_6_last_6',
       'Ast_per_poss_last_6_last_6', 'Week_1', 'Week_18', 'AdjOE',
       'AdjDE', 'AdjEM', 'Seed', 'Trapezoid', 'Diff Win',
       '3PM_diff', 'FT_diff', 'PPPos_diff', 'Orb_diff', 'Tov_diff',
       'rank_diff', 'Pom_diff', 'TOV Margin']

data2024 = data2024[new_order]

data2024.columns

Index(['Season', 'TeamID', 'Win %', 'PPPos', 'PAPPos', 'PPPos Margin', 'FG %',
       'OppFG%', '3PT FG %', '3PTPPos', 'FT %', 'FTPPos', 'OppFTPPos',
       'ORPPos', 'Opp ORPPos', 'DRPG', 'REBPG', 'REB Margin',
       'True Shooting %', 'Effective FG%', 'TOV %', 'TOV Forced %',
       'Foul Margin', 'OppEFG', 'Win_last_6', 'FGM_per_poss_last_6_last_6',
       'FGA_per_poss_last_6_last_6', 'DR_per_poss_last_6_last_6',
       'Ast_per_poss_last_6_last_6', 'Week_1', 'Week_18', 'AdjOE', 'AdjDE',
       'AdjEM', 'Seed', 'Trapezoid', 'Diff Win', '3PM_diff', 'FT_diff',
       'PPPos_diff', 'Orb_diff', 'Tov_diff', 'rank_diff', 'Pom_diff',
       'TOV Margin'],
      dtype='object')

In [340]:
# Initialize a list to store predictions and their IDs
predictions = []

for index, row in submissions.iterrows():
    matchup_id = row['ID']
    _, team1ID, team2ID = map(int, matchup_id.split('_'))
    print(f"Team 1 ID: {team1ID}")
    print(f"Team 2 ID: {team2ID}")
    # Extract team data for the 2023 season
    team1Data = data2024[data2024['TeamID'] == team1ID].iloc[:, 2:].values.flatten()
    team2Data = data2024[data2024['TeamID'] == team2ID].iloc[:, 2:].values.flatten()

    if team1Data.size == 0 or team2Data.size == 0:
        print(f"Skipping missing data for matchup: {matchup_id}")
        continue

    difference = np.subtract(team1Data, team2Data)
    
    # Use the pipeline directly for predictions, which includes scaling and PCA transformation
    prediction_proba = best_pipeline.predict_proba([difference])[:, 1][0]  # Get the probability of the positive class
    predictions.append((matchup_id, prediction_proba))

Team 1 ID: 1101
Team 2 ID: 1102
Team 1 ID: 1101
Team 2 ID: 1103
Team 1 ID: 1101
Team 2 ID: 1104
Team 1 ID: 1101
Team 2 ID: 1105
Team 1 ID: 1101
Team 2 ID: 1106
Team 1 ID: 1101
Team 2 ID: 1107
Team 1 ID: 1101
Team 2 ID: 1108
Team 1 ID: 1101
Team 2 ID: 1110
Team 1 ID: 1101
Team 2 ID: 1111
Team 1 ID: 1101
Team 2 ID: 1112
Team 1 ID: 1101
Team 2 ID: 1113
Team 1 ID: 1101
Team 2 ID: 1114
Team 1 ID: 1101
Team 2 ID: 1115
Team 1 ID: 1101
Team 2 ID: 1116
Team 1 ID: 1101
Team 2 ID: 1117
Team 1 ID: 1101
Team 2 ID: 1119
Team 1 ID: 1101
Team 2 ID: 1120
Team 1 ID: 1101
Team 2 ID: 1122
Team 1 ID: 1101
Team 2 ID: 1123
Team 1 ID: 1101
Team 2 ID: 1124
Team 1 ID: 1101
Team 2 ID: 1125
Team 1 ID: 1101
Team 2 ID: 1126
Team 1 ID: 1101
Team 2 ID: 1127
Team 1 ID: 1101
Team 2 ID: 1129
Team 1 ID: 1101
Team 2 ID: 1130
Team 1 ID: 1101
Team 2 ID: 1131
Team 1 ID: 1101
Team 2 ID: 1132
Team 1 ID: 1101
Team 2 ID: 1133
Team 1 ID: 1101
Team 2 ID: 1135
Team 1 ID: 1101
Team 2 ID: 1136
Team 1 ID: 1101
Team 2 ID: 1137
Team 1 I

Team 1 ID: 1101
Team 2 ID: 1466
Team 1 ID: 1101
Team 2 ID: 1467
Team 1 ID: 1101
Team 2 ID: 1468
Team 1 ID: 1101
Team 2 ID: 1469
Team 1 ID: 1101
Team 2 ID: 1470
Team 1 ID: 1101
Team 2 ID: 1471
Team 1 ID: 1101
Team 2 ID: 1472
Team 1 ID: 1101
Team 2 ID: 1473
Team 1 ID: 1101
Team 2 ID: 1474
Team 1 ID: 1101
Team 2 ID: 1475
Team 1 ID: 1101
Team 2 ID: 1476
Team 1 ID: 1101
Team 2 ID: 1477
Team 1 ID: 1102
Team 2 ID: 1103
Team 1 ID: 1102
Team 2 ID: 1104
Team 1 ID: 1102
Team 2 ID: 1105
Team 1 ID: 1102
Team 2 ID: 1106
Team 1 ID: 1102
Team 2 ID: 1107
Team 1 ID: 1102
Team 2 ID: 1108
Team 1 ID: 1102
Team 2 ID: 1110
Team 1 ID: 1102
Team 2 ID: 1111
Team 1 ID: 1102
Team 2 ID: 1112
Team 1 ID: 1102
Team 2 ID: 1113
Team 1 ID: 1102
Team 2 ID: 1114
Team 1 ID: 1102
Team 2 ID: 1115
Team 1 ID: 1102
Team 2 ID: 1116
Team 1 ID: 1102
Team 2 ID: 1117
Team 1 ID: 1102
Team 2 ID: 1119
Team 1 ID: 1102
Team 2 ID: 1120
Team 1 ID: 1102
Team 2 ID: 1122
Team 1 ID: 1102
Team 2 ID: 1123
Team 1 ID: 1102
Team 2 ID: 1124
Team 1 I

Team 1 ID: 1103
Team 2 ID: 1140
Team 1 ID: 1103
Team 2 ID: 1141
Team 1 ID: 1103
Team 2 ID: 1142
Team 1 ID: 1103
Team 2 ID: 1143
Team 1 ID: 1103
Team 2 ID: 1144
Team 1 ID: 1103
Team 2 ID: 1145
Team 1 ID: 1103
Team 2 ID: 1146
Team 1 ID: 1103
Team 2 ID: 1148
Team 1 ID: 1103
Team 2 ID: 1149
Team 1 ID: 1103
Team 2 ID: 1150
Team 1 ID: 1103
Team 2 ID: 1151
Team 1 ID: 1103
Team 2 ID: 1152
Team 1 ID: 1103
Team 2 ID: 1153
Team 1 ID: 1103
Team 2 ID: 1154
Team 1 ID: 1103
Team 2 ID: 1155
Team 1 ID: 1103
Team 2 ID: 1156
Team 1 ID: 1103
Team 2 ID: 1157
Team 1 ID: 1103
Team 2 ID: 1158
Team 1 ID: 1103
Team 2 ID: 1159
Team 1 ID: 1103
Team 2 ID: 1160
Team 1 ID: 1103
Team 2 ID: 1161
Team 1 ID: 1103
Team 2 ID: 1162
Team 1 ID: 1103
Team 2 ID: 1163
Team 1 ID: 1103
Team 2 ID: 1164
Team 1 ID: 1103
Team 2 ID: 1165
Team 1 ID: 1103
Team 2 ID: 1166
Team 1 ID: 1103
Team 2 ID: 1167
Team 1 ID: 1103
Team 2 ID: 1168
Team 1 ID: 1103
Team 2 ID: 1169
Team 1 ID: 1103
Team 2 ID: 1170
Team 1 ID: 1103
Team 2 ID: 1171
Team 1 I

Team 1 ID: 1104
Team 2 ID: 1159
Team 1 ID: 1104
Team 2 ID: 1160
Team 1 ID: 1104
Team 2 ID: 1161
Team 1 ID: 1104
Team 2 ID: 1162
Team 1 ID: 1104
Team 2 ID: 1163
Team 1 ID: 1104
Team 2 ID: 1164
Team 1 ID: 1104
Team 2 ID: 1165
Team 1 ID: 1104
Team 2 ID: 1166
Team 1 ID: 1104
Team 2 ID: 1167
Team 1 ID: 1104
Team 2 ID: 1168
Team 1 ID: 1104
Team 2 ID: 1169
Team 1 ID: 1104
Team 2 ID: 1170
Team 1 ID: 1104
Team 2 ID: 1171
Team 1 ID: 1104
Team 2 ID: 1172
Team 1 ID: 1104
Team 2 ID: 1173
Team 1 ID: 1104
Team 2 ID: 1174
Team 1 ID: 1104
Team 2 ID: 1175
Team 1 ID: 1104
Team 2 ID: 1176
Team 1 ID: 1104
Team 2 ID: 1177
Team 1 ID: 1104
Team 2 ID: 1178
Team 1 ID: 1104
Team 2 ID: 1179
Team 1 ID: 1104
Team 2 ID: 1180
Team 1 ID: 1104
Team 2 ID: 1181
Team 1 ID: 1104
Team 2 ID: 1182
Team 1 ID: 1104
Team 2 ID: 1183
Team 1 ID: 1104
Team 2 ID: 1184
Team 1 ID: 1104
Team 2 ID: 1185
Team 1 ID: 1104
Team 2 ID: 1186
Team 1 ID: 1104
Team 2 ID: 1187
Team 1 ID: 1104
Team 2 ID: 1188
Team 1 ID: 1104
Team 2 ID: 1189
Team 1 I

Team 1 ID: 1105
Team 2 ID: 1214
Team 1 ID: 1105
Team 2 ID: 1216
Skipping missing data for matchup: 2023_1105_1216
Team 1 ID: 1105
Team 2 ID: 1217
Team 1 ID: 1105
Team 2 ID: 1218
Team 1 ID: 1105
Team 2 ID: 1219
Team 1 ID: 1105
Team 2 ID: 1220
Team 1 ID: 1105
Team 2 ID: 1221
Team 1 ID: 1105
Team 2 ID: 1222
Team 1 ID: 1105
Team 2 ID: 1223
Team 1 ID: 1105
Team 2 ID: 1224
Team 1 ID: 1105
Team 2 ID: 1225
Team 1 ID: 1105
Team 2 ID: 1226
Team 1 ID: 1105
Team 2 ID: 1227
Team 1 ID: 1105
Team 2 ID: 1228
Team 1 ID: 1105
Team 2 ID: 1229
Team 1 ID: 1105
Team 2 ID: 1230
Team 1 ID: 1105
Team 2 ID: 1231
Team 1 ID: 1105
Team 2 ID: 1232
Team 1 ID: 1105
Team 2 ID: 1233
Team 1 ID: 1105
Team 2 ID: 1234
Team 1 ID: 1105
Team 2 ID: 1235
Team 1 ID: 1105
Team 2 ID: 1236
Team 1 ID: 1105
Team 2 ID: 1237
Team 1 ID: 1105
Team 2 ID: 1238
Team 1 ID: 1105
Team 2 ID: 1239
Team 1 ID: 1105
Team 2 ID: 1240
Team 1 ID: 1105
Team 2 ID: 1241
Team 1 ID: 1105
Team 2 ID: 1242
Team 1 ID: 1105
Team 2 ID: 1243
Team 1 ID: 1105
Team 2

...

Team 1 ID: 1449
Team 2 ID: 1461
Team 1 ID: 1449
Team 2 ID: 1462
Team 1 ID: 1449
Team 2 ID: 1463
Team 1 ID: 1449
Team 2 ID: 1464
Team 1 ID: 1449
Team 2 ID: 1465
Team 1 ID: 1449
Team 2 ID: 1466
Team 1 ID: 1449
Team 2 ID: 1467
Team 1 ID: 1449
Team 2 ID: 1468
Team 1 ID: 1449
Team 2 ID: 1469
Team 1 ID: 1449
Team 2 ID: 1470
Team 1 ID: 1449
Team 2 ID: 1471
Team 1 ID: 1449
Team 2 ID: 1472
Team 1 ID: 1449
Team 2 ID: 1473
Team 1 ID: 1449
Team 2 ID: 1474
Team 1 ID: 1449
Team 2 ID: 1475
Team 1 ID: 1449
Team 2 ID: 1476
Team 1 ID: 1449
Team 2 ID: 1477
Team 1 ID: 1450
Team 2 ID: 1451
Team 1 ID: 1450
Team 2 ID: 1452
Team 1 ID: 1450
Team 2 ID: 1453
Team 1 ID: 1450
Team 2 ID: 1454
Team 1 ID: 1450
Team 2 ID: 1455
Team 1 ID: 1450
Team 2 ID: 1456
Team 1 ID: 1450
Team 2 ID: 1457
Team 1 ID: 1450
Team 2 ID: 1458
Team 1 ID: 1450
Team 2 ID: 1459
Team 1 ID: 1450
Team 2 ID: 1460
Team 1 ID: 1450
Team 2 ID: 1461
Team 1 ID: 1450
Team 2 ID: 1462
Team 1 ID: 1450
Team 2 ID: 1463
Team 1 ID: 1450
Team 2 ID: 1464
Team 1 I

Team 1 ID: 1473
Team 2 ID: 1475
Team 1 ID: 1473
Team 2 ID: 1476
Team 1 ID: 1473
Team 2 ID: 1477
Team 1 ID: 1474
Team 2 ID: 1475
Team 1 ID: 1474
Team 2 ID: 1476
Team 1 ID: 1474
Team 2 ID: 1477
Team 1 ID: 1475
Team 2 ID: 1476
Team 1 ID: 1475
Team 2 ID: 1477
Team 1 ID: 1476
Team 2 ID: 1477
Team 1 ID: 3101
Team 2 ID: 3102
Skipping missing data for matchup: 2023_3101_3102
Team 1 ID: 3101
Team 2 ID: 3103
Skipping missing data for matchup: 2023_3101_3103
Team 1 ID: 3101
Team 2 ID: 3104
Skipping missing data for matchup: 2023_3101_3104
Team 1 ID: 3101
Team 2 ID: 3105
Skipping missing data for matchup: 2023_3101_3105
Team 1 ID: 3101
Team 2 ID: 3106
Skipping missing data for matchup: 2023_3101_3106
Team 1 ID: 3101
Team 2 ID: 3107
Skipping missing data for matchup: 2023_3101_3107
Team 1 ID: 3101
Team 2 ID: 3108
Skipping missing data for matchup: 2023_3101_3108
Team 1 ID: 3101
Team 2 ID: 3110
Skipping missing data for matchup: 2023_3101_3110
Team 1 ID: 3101
Team 2 ID: 3111
Skipping missing data fo

Skipping missing data for matchup: 2023_3115_3279
Team 1 ID: 3115
Team 2 ID: 3280
Skipping missing data for matchup: 2023_3115_3280
Team 1 ID: 3115
Team 2 ID: 3281
Skipping missing data for matchup: 2023_3115_3281
Team 1 ID: 3115
Team 2 ID: 3282
Skipping missing data for matchup: 2023_3115_3282
Team 1 ID: 3115
Team 2 ID: 3283
Skipping missing data for matchup: 2023_3115_3283
Team 1 ID: 3115
Team 2 ID: 3284
Skipping missing data for matchup: 2023_3115_3284
Team 1 ID: 3115
Team 2 ID: 3285
Skipping missing data for matchup: 2023_3115_3285
Team 1 ID: 3115
Team 2 ID: 3286
Skipping missing data for matchup: 2023_3115_3286
Team 1 ID: 3115
Team 2 ID: 3287
Skipping missing data for matchup: 2023_3115_3287
Team 1 ID: 3115
Team 2 ID: 3288
Skipping missing data for matchup: 2023_3115_3288
Team 1 ID: 3115
Team 2 ID: 3290
Skipping missing data for matchup: 2023_3115_3290
Team 1 ID: 3115
Team 2 ID: 3291
Skipping missing data for matchup: 2023_3115_3291
Team 1 ID: 3115
Team 2 ID: 3292
Skipping missing

Skipping missing data for matchup: 2023_3197_3427
Team 1 ID: 3197
Team 2 ID: 3428
Skipping missing data for matchup: 2023_3197_3428
Team 1 ID: 3197
Team 2 ID: 3429
Skipping missing data for matchup: 2023_3197_3429
Team 1 ID: 3197
Team 2 ID: 3430
Skipping missing data for matchup: 2023_3197_3430
Team 1 ID: 3197
Team 2 ID: 3431
Skipping missing data for matchup: 2023_3197_3431
Team 1 ID: 3197
Team 2 ID: 3433
Skipping missing data for matchup: 2023_3197_3433
Team 1 ID: 3197
Team 2 ID: 3434
Skipping missing data for matchup: 2023_3197_3434
Team 1 ID: 3197
Team 2 ID: 3435
Skipping missing data for matchup: 2023_3197_3435
Team 1 ID: 3197
Team 2 ID: 3436
Skipping missing data for matchup: 2023_3197_3436
Team 1 ID: 3197
Team 2 ID: 3437
Skipping missing data for matchup: 2023_3197_3437
Team 1 ID: 3197
Team 2 ID: 3438
Skipping missing data for matchup: 2023_3197_3438
Team 1 ID: 3197
Team 2 ID: 3439
Skipping missing data for matchup: 2023_3197_3439
Team 1 ID: 3197
Team 2 ID: 3441
Skipping missing

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [341]:
# Convert predictions into a DataFrame
predictions_df = pd.DataFrame(predictions, columns=['ID', 'Pred'])

# Merge or simply replace the Pred column in submissions with predictions
# Assuming submissions and predictions_df are aligned and predictions_df doesn't miss any row from submissions
submission_df = pd.merge(submissions[['ID']], predictions_df, on='ID', how='left')

# Handling any potential missing predictions due to skipped matchups
submission_df['Pred'].fillna(0.5, inplace=True)  # Default value for missing predictions


In [342]:
submission_df.to_csv('data/CLASSIFIEDPREDICTIONS.csv', index=False)


In [343]:
submission_df

ID      Pred
0       2023_1101_1102  0.954511
1       2023_1101_1103  0.029468
2       2023_1101_1104  0.086189
3       2023_1101_1105  0.228887
4       2023_1101_1106  0.577464
...                ...       ...
130678  2023_3474_3476  0.500000
130679  2023_3474_3477  0.500000
130680  2023_3475_3476  0.500000
130681  2023_3475_3477  0.500000
130682  2023_3476_3477  0.500000

[130683 rows x 2 columns]

In [45]:
def predict_matchup(team1_name, team2_name, teams_df, predictions_df1, predictions_df2, predictions_df3):
    # Find team IDs based on team names
    team1_id = teams_df[teams_df['TeamName'] == team1_name]['TeamID'].values[0]
    team2_id = teams_df[teams_df['TeamName'] == team2_name]['TeamID'].values[0]
    print(team1_id)
    print(team2_id)
    # Construct the matchup ID in the format 'season_team1ID_team2ID'
    # Assuming the season is 2023 as per previous context
    if team1_id < team2_id:
        matchup_id = f'2023_{team1_id}_{team2_id}'
    else:
        matchup_id = f'2023_{team2_id}_{team1_id}'
    
    # Retrieve the prediction for the matchup
    prediction = predictions_df1[predictions_df1['ID'] == matchup_id]['Pred'].values[0]                                                                 
    prediction += predictions_df2[predictions_df2['ID'] == matchup_id]['Pred'].values[0]                                                                  
    prediction += predictions_df3[predictions_df3['ID'] == matchup_id]['Pred'].values[0]                                                                     

    prediction /= 3
    # Determine the winner based on the prediction
    if prediction > 0.5:
        winner = team1_name if team1_id < team2_id else team2_name
    else:
        winner = team2_name if team1_id < team2_id else team1_name
        prediction = 1 - prediction
    
    # Adjust the winning probability to reflect the winner
    winning_prob = prediction     
    
    return winner, winning_prob * 100

In [46]:
# Load necessary data
teams = pd.read_csv("data/MTeams.csv")
submission_df1 = pd.read_csv('data/CLASSIFIEDPREDICTIONS.csv')
submission_df2 = pd.read_csv('data/LR_final_predictions_2024.csv')
submission_df3 = pd.read_csv('data/final_predictions_2024.csv')


In [49]:
# Example usage
team1_name = "Wisconsin"
team2_name = "James Madison" 
winner, winning_prob = predict_matchup(team1_name, team2_name, teams, submission_df1, submission_df2, submission_df3)

print(f"Winner: {winner} with a probability of {winning_prob:.2f}%")

1458
1241
Winner: Wisconsin with a probability of 71.61%


In [33]:
def print_team_matchups(team_name, teams_df, predictions_df):
    # Find the TeamID for the given team name
    team_id = str(teams_df[teams_df['TeamName'] == team_name]['TeamID'].iloc[0])

    print(f"Matchups for {team_name} (TeamID: {team_id}):")

    # Iterate over each row in predictions_df
    for _, row in predictions_df.iterrows():
        matchup_id = row['ID']
        prediction = row['Pred']
        _, first_team_id, second_team_id = matchup_id.split('_')

        # Check if the current team_id matches either team in the matchup
        if team_id in [first_team_id, second_team_id]:
            # Identify the opponent's ID and then their name
            opponent_id = second_team_id if first_team_id == team_id else first_team_id
            opponent_name = teams_df[teams_df['TeamID'] == int(opponent_id)]['TeamName'].iloc[0]

            # Adjust the prediction value based on team order
            if first_team_id != team_id:
                prediction = 1 - prediction  # Flip the prediction if the team is the second team

            # Determine the matchup description
            if first_team_id == team_id:
                matchup_description = f"{team_name} vs. {opponent_name}"
            else:
                matchup_description = f"{opponent_name} vs. {team_name}"

            # Print the matchup details with adjusted prediction
            print(f"{matchup_id}: {matchup_description} - Prediction: {prediction:.2f}")


In [50]:
# Usage example
team_name = "Wisconsin"  # Example team name
print_team_matchups(team_name, teams, submission_df1)

Matchups for Wisconsin (TeamID: 1458):
2023_1101_1458: Abilene Chr vs. Wisconsin - Prediction: 0.99
2023_1102_1458: Air Force vs. Wisconsin - Prediction: 0.99
2023_1103_1458: Akron vs. Wisconsin - Prediction: 0.98
2023_1104_1458: Alabama vs. Wisconsin - Prediction: 0.94
2023_1105_1458: Alabama A&M vs. Wisconsin - Prediction: 0.99
2023_1106_1458: Alabama St vs. Wisconsin - Prediction: 0.89
2023_1107_1458: SUNY Albany vs. Wisconsin - Prediction: 0.99
2023_1108_1458: Alcorn St vs. Wisconsin - Prediction: 1.00
2023_1110_1458: American Univ vs. Wisconsin - Prediction: 0.99
2023_1111_1458: Appalachian St vs. Wisconsin - Prediction: 0.73
2023_1112_1458: Arizona vs. Wisconsin - Prediction: 0.01
2023_1113_1458: Arizona St vs. Wisconsin - Prediction: 0.97
2023_1114_1458: Ark Little Rock vs. Wisconsin - Prediction: 0.99
2023_1115_1458: Ark Pine Bluff vs. Wisconsin - Prediction: 0.99
2023_1116_1458: Arkansas vs. Wisconsin - Prediction: 0.98
2023_1117_1458: Arkansas St vs. Wisconsin - Prediction: 0

2023_1394_1458: TAM C. Christi vs. Wisconsin - Prediction: 0.98
2023_1395_1458: TCU vs. Wisconsin - Prediction: 0.55
2023_1396_1458: Temple vs. Wisconsin - Prediction: 0.99
2023_1397_1458: Tennessee vs. Wisconsin - Prediction: 0.90
2023_1398_1458: Tennessee St vs. Wisconsin - Prediction: 0.99
2023_1399_1458: Tennessee Tech vs. Wisconsin - Prediction: 1.00
2023_1400_1458: Texas vs. Wisconsin - Prediction: 0.34
2023_1401_1458: Texas A&M vs. Wisconsin - Prediction: 0.54
2023_1402_1458: Texas St vs. Wisconsin - Prediction: 0.97
2023_1403_1458: Texas Tech vs. Wisconsin - Prediction: 0.63
2023_1404_1458: TN Martin vs. Wisconsin - Prediction: 0.99
2023_1405_1458: Toledo vs. Wisconsin - Prediction: 0.99
2023_1406_1458: Towson vs. Wisconsin - Prediction: 0.98
2023_1407_1458: Troy vs. Wisconsin - Prediction: 0.93
2023_1408_1458: Tulane vs. Wisconsin - Prediction: 0.99
2023_1409_1458: Tulsa vs. Wisconsin - Prediction: 0.98
2023_1410_1458: UTRGV vs. Wisconsin - Prediction: 0.99
2023_1411_1458: TX 